![](lu_decomposition.png)

#### Import dependencies

In [1]:
import numpy as np
import numpy.linalg as LA
import scipy as sp
from time import perf_counter as pc

### Modules

#### Generate square matrix with random values

In [16]:
def get_matrix(n):
    #np.random.seed(32)
    return np.random.uniform(-100,100,(n, n))

#### Interchange of rows
Formed my interchanging `i`th and `j`th rows of an order `n` matrix.

In [3]:
def swap_row(A,i,j):
    A[[i,j]] = A[[j,i]]
    return A

### Permutation matrix generator
Formed my interchanging `i`th and `j`th rows of an Identity matrix of order `n`

In [4]:
def list_to_permulation_matrix(n, permutation_list):
    [i, j] = permutation_list
    return swap_row(np.eye(n),i,j)

#### Elimination matrix generator
Formed by replacing `i+1` to `n-1`th element of `i`th column with the pivot ratio factors.

In [5]:
def list_to_elimination_matrix(n, elimination_list):
    i, arr = elimination_list
    E = np.eye(n)
    E[i+1:,i] = np.array(arr)
    return E

### Transforming `A` to Upper Triangular matrix `U`
**i/p** : Matrix `A`

**o/p** : Matrix `U` and `P`<sub>`1`</sub>`L`<sub>`1`</sub>`P`<sub>`2`</sub>`L`<sub>`2`</sub>...`P`<sub>`k`</sub>`L`<sub>`k`</sub>

`P` -> `U`, where, `P x A = L x U`

Using Gaussian Elimination method

In [6]:
def A_to_U_transform(A):
    factorized_matrices_of_L_inv = []
    degree = A.shape[0]
    for row in range(degree-1):     
        pivot_search_array = abs(A[row:,row])
        pivot_index = row + np.argmax(pivot_search_array)
        if pivot_index != row:
            A = swap_row(A,row,pivot_index)
            factorized_matrices_of_L_inv.append(('P', [row, pivot_index])) 
        normalised_col = []
        
        for row_below in range(row+1, degree):
            pivot_ratio = -A[row_below,row] / A[row,row]
            normalised_col.append(pivot_ratio)
            A[row_below] += A[row] * pivot_ratio
        print(A)
        factorized_matrices_of_L_inv.append(('L',[row, normalised_col]))
    return A, factorized_matrices_of_L_inv

#### Calculation Permutation matrix `P` and Lower Triangular matrix `L`

**i/p** : Degree of the desired matrices(`n`) and `P`<sub>`1`</sub>`L`<sub>`1`</sub>`P`<sub>`2`</sub>`L`<sub>`2`</sub>...`P`<sub>`k`</sub>`L`<sub>`k`</sub>

**o/p** : Matrix `P` and `L`

where, `P x A = L x U`

In [7]:
def solve_for_P_and_L(degree, permute_eliminate_matrix_arr):
    L = list_to_elimination_matrix(degree, permute_eliminate_matrix_arr[-1][1])
    P = np.eye(degree)
    for operation in permute_eliminate_matrix_arr[-2::-1]:
        if operation[0] == 'P':
            [i,j] = operation[1]
            P = swap_row(P.copy(),i,j)
        elif operation[0] == 'L':
            arr = operation[1]
            P_inv = LA.inv(P.copy())
            L_ = P @ list_to_elimination_matrix(degree, arr) @ P_inv
            L = L@L_
    return P, LA.inv(L)

#### LU decomposition performance measure with multiple degree matrices

In [19]:
#%%timeit
degree_array = [10000]

def LU_perf_measure(degree_array):
    degree_performance = {}
    # Solve for PAx = LUx = b
    A_matrices = {}
    U_matrices = {}
    L_matrices = {}
    P_matrices = {}
    matrix_norms = {}

    for degree in degree_array:
        A_matrices[degree] = get_matrix(degree)

        start = pc()
        U_matrices[degree], permute_eliminate_matrix_arr = A_to_U_transform(A_matrices[degree].copy())
        P_matrices[degree], L_matrices[degree] = solve_for_P_and_L(degree, permute_eliminate_matrix_arr)
        degree_performance[degree] = (pc()-start)*10**6

    for degree in degree_array:
        diff = (P_matrices[degree]@A_matrices[degree]) - (L_matrices[degree]@U_matrices[degree])    # PA-LU
        matrix_norms[degree] = {'first':LA.norm(diff,1),'inf':LA.norm(diff,np.inf),'fro':LA.norm(diff,'fro')}

    return (degree_performance, P_matrices, A_matrices, L_matrices, U_matrices, matrix_norms)

In [21]:
(perf,p,a,l,u,n) = LU_perf_measure([10000])

[[-99.98005038 -10.68056645  81.84254463 ...  -0.19069964  32.14434307
   56.93006858]
 [  0.         -57.97760064 -83.97016928 ...  28.12138275 -32.72434174
    9.08002294]
 [  0.         -98.62161864  -9.46369156 ...  -0.91566098 124.78218457
   84.7141669 ]
 ...
 [  0.         -96.83918469  95.16595195 ...  39.67149224 -41.95877196
   23.14814469]
 [  0.         -70.68080763  63.71405609 ... -90.66480172 -53.27961914
  113.10814751]
 [  0.          78.18146945  91.58768894 ...  23.50170546 -49.15448417
   12.2815193 ]]
[[ -99.98005038  -10.68056645   81.84254463 ...   -0.19069964
    32.14434307   56.93006858]
 [   0.         -110.2656151     9.6074865  ...    8.0235034
   -60.43403154  -33.0716181 ]
 [   0.            0.          -18.05663206 ...   -8.09188624
   178.83441116  114.29343787]
 ...
 [   0.            0.           86.72831563 ...   32.6249662
    11.11654383   52.19281588]
 [   0.            0.           57.55560947 ...  -95.8079073
   -14.54110438  134.30721917]
 [   

#### Example

In [9]:
a, u = np.array([[1,-2,3],[9,34,36],[2,-45,9]]).astype('float32'),np.array([[3,7,90],[0,23,5],[0,0,9]]).astype('float64')

In [10]:
u,l = A_to_U_transform(a.copy())

[[  9.         34.         36.       ]
 [  0.         -5.7777777  -1.       ]
 [  0.        -52.555557    1.       ]]
[[  9.         34.         36.       ]
 [  0.        -52.555557    1.       ]
 [  0.          0.         -1.1099366]]


In [11]:
p,L = solve_for_P_and_L(3,l)

In [12]:
a

array([[  1.,  -2.,   3.],
       [  9.,  34.,  36.],
       [  2., -45.,   9.]], dtype=float32)

In [13]:
p

array([[0., 0., 1.],
       [1., 0., 0.],
       [0., 1., 0.]])

In [14]:
print(p@a)
print(L@u)

[[  2. -45.   9.]
 [  1.  -2.   3.]
 [  9.  34.  36.]]
[[  9.          34.          36.        ]
 [  2.00000001 -45.00000164   9.00000006]
 [  1.00000001  -2.00000003   3.00000001]]


`PA` matrix has a different sequence of rows compared to `LU`.
### Please Check !!